In [94]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.figure_factory as ff
from urllib.parse import urlparse
import string
from nltk.stem import PorterStemmer
from nltk.corpus import stopwords
import nltk
import re

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)
pd.set_option("display.max_colwidth", None)

# Datasets joining and reading

In [95]:
starting_points = {'parsed\\parsed_tweets_gossipcop_fake.csv': 'gossipcop-699303448',
                    'parsed\\parsed_tweets_gossipcop_real.csv': 'gossipcop-881670',
                    'parsed\\parsed_tweets_politifact_fake.csv': 'politifact15135',
                    'parsed\\parsed_tweets_politifact_real.csv': 'politifact954'}

parsed_files_paths = list(starting_points.keys())

dfs_dict = {}

columns = ['news_id','tweet_id','text','label']

for parsed_file_path in parsed_files_paths:
    # for tweets df

    words = parsed_file_path.split('\\')[1].split('.')[0].split('_')
    words.pop(0)
    df_name_tweets = '_'.join(words)

    dfs_dict[df_name_tweets] = pd.read_csv(parsed_file_path,header=None, names=columns,encoding='utf-8')

    # for news_df

    words.pop(0)
    df_name_news = '_'.join(words)

    file_path_news = f'datasets/FakeNewsNet/{df_name_news}.csv'

    dfs_dict[df_name_news] = pd.read_csv(file_path_news,encoding='utf-8')

In [96]:
dfs_dict.keys()

dict_keys(['tweets_gossipcop_fake', 'gossipcop_fake', 'tweets_gossipcop_real', 'gossipcop_real', 'tweets_politifact_fake', 'politifact_fake', 'tweets_politifact_real', 'politifact_real'])

In [97]:
dfs_dict['politifact_real'].head()

id                                                                                                                                           news_url                                                                           title  \
0  politifact14984                                                                                                                          http://www.nfib-sbet.org/                                     National Federation of Independent Business   
1  politifact12944                                                                                               http://www.cq.com/doc/newsmakertranscripts-4942265?3                                                     comments in Fayetteville NC   
2    politifact333  https://web.archive.org/web/20080204072132/http://www.rockymountainnews.com:80/news/2008/feb/02/romney-tells-denver-crowd-he-can-salvage-economy/  Romney makes pitch, hoping to close deal : Elections : The Rocky Mountain News   
3   politifact4358     https://web.archive.org/web/20110811143753/http://www.dems.gov/press/democratic-leaders-say-house-democrats-are-united-against-gop-default-act       Democratic Leaders Say House Democrats Are United Against GOP Default Act   
4    politifact779                                                https://web.archive.org/web/20070820164107/http://www.whitehouse.gov/omb/budget/fy2008/outlook.html                                 Budget of the United States Government, FY 2008   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

In [98]:
dfs_dict['gossipcop_fake'].head()

id                                                                                                                                                             news_url                                                                                               title  \
0  gossipcop-2493749932                                                                   www.dailymail.co.uk/tvshowbiz/article-5874213/Did-Miley-Cyrus-Liam-Hemsworth-secretly-married.html                                            Did Miley Cyrus and Liam Hemsworth secretly get married?   
1  gossipcop-4580247171                                                                hollywoodlife.com/2018/05/05/paris-jackson-cara-delevingne-matching-outfits-night-out-nyc-dating-pic/  Paris Jackson & Cara Delevingne Enjoy Night Out In Matching Outfits: They Have ‘Amazing Chemistry’   
2   gossipcop-941805037                                                                                                 variety.com/2017/biz/news/tax-march-donald-trump-protest-1202031487/                                               Celebrities Join Tax March in Protest of Donald Trump   
3  gossipcop-2547891536  www.dailymail.co.uk/femail/article-3499192/Do-blondes-REALLY-fun-Cindy-Crawford-s-model-daughter-Kaia-Gerber-puts-theory-test-peroxide-wig-dining-Harry-Styles.html                    Cindy Crawford's daughter Kaia Gerber wears a wig after dining with Harry Styles   
4  gossipcop-5476631226                                                                                                   variety.com/2018/film/news/list-2018-oscar-nominations-1202668757/                                                       Full List of 2018 Oscar Nominations – Variety   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   tweet_ids  
0  284329075902926848\t284332744559968256\t284335412590297089\t284359918792880128\t284385385151332353\t284456388833452032\t284644878267318273\t284656558963564545\t284705391965794304\t284705391957401601\t284762425553723392\t284766089827721217\t284769766806257664\t284769769490620416\t284769775442337792

In [99]:
dfs_dict['tweets_gossipcop_fake'].merge(dfs_dict['gossipcop_fake'],left_on='news_id',right_on='id',how='left').head()

news_id            tweet_id                                                                                                                                      text  label                    id                                                                                            news_url                                                     title  \
0  gossipcop-2493749932  284332744559968256                                   Did Miley Cyrus and Liam Hemsworth secretly get married? | In Case You Didn't Know http://t.co/daJAmp83      0  gossipcop-2493749932  www.dailymail.co.uk/tvshowbiz/article-5874213/Did-Miley-Cyrus-Liam-Hemsworth-secretly-married.html  Did Miley Cyrus and Liam Hemsworth secretly get married?   
1  gossipcop-2493749932  284335412590297089                                                             Did Miley Cyrus and Liam Hemsworth secretly get married? http://t.co/KwgEiKOn      0  gossipcop-2493749932  www.dailymail.co.uk/tvshowbiz/article-5874213/Did-Miley-Cyrus-Liam-Hemsworth-secretly-married.html  Did Miley Cyrus and Liam Hemsworth secretly get married?   
2  gossipcop-2493749932  284359918792880128  Afternoon Tea – Daily Link Roundup: Did Miley Cyrus and Liam Hemsworth secretly get married? – Celebitchy Mila K... http://t.co/vuJL1TB4      0  gossipcop-2493749932  www.dailymail.co.uk/tvshowbiz/article-5874213/Did-Miley-Cyrus-Liam-Hemsworth-secretly-married.html  Did Miley Cyrus and Liam Hemsworth secretly get married?   
3  gossipcop-2493749932  284385385151332353                                                             Did Miley Cyrus and Liam Hemsworth secretly get married? http://t.co/KJnBxgvk      0  gossipcop-2493749932  www.dailymail.co.uk/tvshowbiz/article-5874213/Did-Miley-Cyrus-Liam-Hemsworth-secretly-married.html  Did Miley Cyrus and Liam Hemsworth secretly get married?   
4  gossipcop-2493749932  284456388833452032                                                           "Did Miley Cyrus and Liam Hemsworth secretly get married?" http://t.co/2rqbmSJn      0  gossipcop-2493749932  www.dailymail.co.uk/tvshowbiz/article-5874213/Did-Miley-Cyrus-Liam-Hemsworth-secretly-married.html  Did Miley Cyrus and Liam Hemsworth secretly get married?   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [100]:
#fake distribution

dfs_dict['gossipcop_fake']['label']=0
dfs_dict['gossipcop_real']['label']=1
dfs_dict['politifact_fake']['label']=0
dfs_dict['politifact_real']['label']=1

news_dfs = [dfs_dict['gossipcop_fake'],dfs_dict['gossipcop_real'],dfs_dict['politifact_fake'],dfs_dict['politifact_real']]

complete_news_df = pd.concat(news_dfs)


In [101]:
complete_news_df.sample(5)

id                                                                                                                                           news_url                                                                        title  \
4861   gossipcop-9720326723                                                                   www.refinery29.com/2017/08/169831/bella-hadid-victorias-secret-fashion-show-2017       Bella Hadid Will Be Walking This Year's Victoria's Secret Fashion Show   
16415      gossipcop-921793  https://calgarysun.com/entertainment/celebrity/how-blake-shelton-and-kelly-clarkson-made-adam-levine-cry/wcm/7406b6ae-d592-405e-9075-514eb9af11d9                    How Blake Shelton and Kelly Clarkson made Adam Levine cry   
8476       gossipcop-901374                                                        https://www.etonline.com/rob-dyrdek-welcomes-baby-girl-wife-bryiana-find-out-her-name-93314        Rob Dyrdek Welcomes Baby Girl With Wife Bryiana -- Find Out Her Name!   
11873      gossipcop-905253               https://www.npr.org/sections/thetwo-way/2018/01/10/576994537/james-franco-denies-sexual-misconduct-claims-saying-theyre-not-accurate  James Franco Denies Sexual Misconduct Claims, Saying They're 'Not Accurate'   
11115      gossipcop-952908                                             https://www.usatoday.com/story/money/2018/07/18/lays-tastes-america-new-flavors-launch-test/788797002/  Fried-pickle potato chips? We taste tested Frito Lay's region-themed snacks   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [102]:
px.bar(complete_news_df['label'].value_counts(),labels={'index':'News label', 'value':'Number of News'})

In [103]:
def count_number_of_tweets(string_object):
    try:
        return string_object.split('\t').__len__()
    except:
        return 0 
    

def count_number_of_words(string_object):
    try:
        return string_object.split().__len__()
    except:
        return 0 

In [104]:
complete_news_df['number_of_tweets'] = complete_news_df['tweet_ids'].apply(count_number_of_tweets)

In [105]:
complete_news_df['number_of_tweets'].sum()

2063442

In [106]:
complete_news_df.drop(columns=['tweet_ids'],inplace=True)

In [107]:


def get_domain(url):
    try:
        if not url.startswith('http'):
            url= 'http://' + url
        return urlparse(url).netloc
    except:
        return np.nan

In [108]:
complete_news_df['domain'] = complete_news_df['news_url'].apply(get_domain)

In [109]:
complete_news_df['Title Lenght'] = complete_news_df['title'].apply(count_number_of_words)
complete_news_df['Title Lenght'].head()

0     9
1    15
2     9
3    13
4     8
Name: Title Lenght, dtype: int64

In [110]:

group_1 = complete_news_df[complete_news_df['label']==0]['Title Lenght'].values
group_2 = complete_news_df[complete_news_df['label']==1]['Title Lenght'].values
X = [group_1,group_2]
group_labels = [f'Fake Article Titles Lenght',f'True Article Titles Lenght']
fig = ff.create_distplot(X,group_labels=group_labels,show_hist=False)
fig.show()

In [111]:
complete_news_df.head()

id                                                                                                                                                             news_url                                                                                               title  label  number_of_tweets               domain  Title Lenght
0  gossipcop-2493749932                                                                   www.dailymail.co.uk/tvshowbiz/article-5874213/Did-Miley-Cyrus-Liam-Hemsworth-secretly-married.html                                            Did Miley Cyrus and Liam Hemsworth secretly get married?      0                97  www.dailymail.co.uk             9
1  gossipcop-4580247171                                                                hollywoodlife.com/2018/05/05/paris-jackson-cara-delevingne-matching-outfits-night-out-nyc-dating-pic/  Paris Jackson & Cara Delevingne Enjoy Night Out In Matching Outfits: They Have ‘Amazing Chemistry’      0                15    hollywoodlife.com            15
2   gossipcop-941805037                                                                                                 variety.com/2017/biz/news/tax-march-donald-trump-protest-1202031487/                                               Celebrities Join Tax March in Protest of Donald Trump      0                86          variety.com             9
3  gossipcop-2547891536  www.dailymail.co.uk/femail/article-3499192/Do-blondes-REALLY-fun-Cindy-Crawford-s-model-daughter-Kaia-Gerber-puts-theory-test-peroxide-wig-dining-Harry-Styles.html                    Cindy Crawford's daughter Kaia Gerber wears a wig after dining with Harry Styles      0                14  www.dailymail.co.uk            13
4  gossipcop-5476631226                                                                                                   variety.com/2018/film/news/list-2018-oscar-nominations-1202668757/                                                       Full List of 2018 Oscar Nominations – Variety      0                66          variety.com             8

In [21]:
#temp_df = pd.pivot_table(complete_news_df,columns=['label','domain'],aggfunc='count',fill_value=0)
temp_df = complete_news_df.groupby(['label','domain']).size()
temp_df = temp_df.unstack(fill_value=0).stack()
temp_df = temp_df.rename('Count').reset_index().fillna(0)
total_df = temp_df.groupby('domain').sum().rename(columns={'Count':'Total'}).reset_index()
total_df
temp_df = temp_df.merge(total_df
              [['domain','Total']],
              left_on='domain',
              right_on='domain',
              how='left')
temp_df.sort_values(by=['Total'],ascending=False,inplace=True)
px.bar(temp_df,x='domain',color='label',y='Count',height=600)

In [114]:
temp_df['Frequency'] = temp_df['Count']/temp_df['Total']
temp_df = temp_df.merge(temp_df[temp_df['label']==1][['domain','Frequency']].rename(columns={'Frequency':'FrequencyPositive'}),left_on='domain',right_on='domain',how='left')
temp_df = temp_df.merge(temp_df[temp_df['label']==0][['domain','Frequency']].rename(columns={'Frequency':'FrequencyNegative'}),left_on='domain',right_on='domain',how='left')
temp_df.head(10)

label                     domain  Count  Total  Frequency  FrequencyPositive_x  FrequencyNegative_x  FrequencyPositive_y  FrequencyNegative_y  FrequencyPositive  FrequencyNegative
0      1            www.eonline.com      0    154        0.0                  0.0                  1.0                  0.0                  1.0                0.0                1.0
1      1               www.imdb.com      0    145        0.0                  0.0                  1.0                  0.0                  1.0                0.0                1.0
2      1   www.nationalenquirer.com      0     53        0.0                  0.0                  1.0                  0.0                  1.0                0.0                1.0
3      1           yournewswire.com      0     25        0.0                  0.0                  1.0                  0.0                  1.0                0.0                1.0
4      1         www.celebitchy.com      0     21        0.0                  0.0                  1.0                  0.0                  1.0                0.0                1.0
5      1  www.celebdirtylaundry.com      0     21        0.0                  0.0                  1.0                  0.0                  1.0                0.0                1.0
6      1        www.pressreader.com      0     20        0.0                  0.0                  1.0                  0.0                  1.0                0.0                1.0
7      1           starmagazine.com      0     16        0.0                  0.0                  1.0                  0.0                  1.0                0.0                1.0
8      1        www.dailymotion.com      0     12        0.0                  0.0                  1.0                  0.0                  1.0                0.0                1.0
9      1            www.magzter.com      0     10        0.0                  0.0                  1.0                  0.0                  1.0                0.0                1.0

In [115]:
temp_df.sort_values(['FrequencyNegative','label'],inplace=True,ascending=False)
REFERENCES = 15
px.bar(temp_df[temp_df['Total']>REFERENCES],x='domain',color='label',y='Frequency',height=600,title=f'Websites having more than {REFERENCES} references')

In [116]:
temp_df.sort_values(['FrequencyNegative','label'],inplace=True,ascending=False)
px.bar(temp_df[temp_df['Total']<REFERENCES],x='domain',color='label',y='Frequency',height=600,title=f'Websites having less than {REFERENCES} references')

In [117]:
# density of fake news in sites where total less or equal 30
# density of fake news in sites where total more than 30

DIVIDER = 50
group_1 = temp_df[temp_df['Total']>DIVIDER]['FrequencyNegative'].values
group_2 = temp_df[temp_df['Total']<=DIVIDER]['FrequencyNegative'].values
X = [group_1,group_2]
group_labels = [f'Sites having more than {DIVIDER} references',f'Sites having less than {DIVIDER} references']
fig = ff.create_distplot(X,group_labels=group_labels,show_hist=False)
fig.update_layout(title='Negative Frequency')
fig.show()

In [118]:
px.scatter(temp_df[temp_df['label']==1],x='Total',y='FrequencyNegative',opacity=0.2)

# Creating data processing pipeline

In [149]:

nltk.download('stopwords')
stemmer = PorterStemmer()
stop_words = set(stopwords.words('english'))

def preprocess_text_for_column(dataframe,column):
    # remove twitter links
    dataframe[column]  = dataframe[column].apply(lambda x: re.sub(r'http\S+', '', x))
    # remove punctuation
    dataframe[column] = dataframe[column].str.replace('[{}]'.format(string.punctuation), '')
    # remove special characters
    dataframe[column] = dataframe[column].str.replace('[^a-zA-Z0-9\s]', '')
    # remove whitespaces
    dataframe[column] = dataframe[column].str.replace(r'\s+', ' ', regex=True)
    # additionaly remove line start and end spaces
    dataframe[column] = dataframe[column].str.strip()
    # remove stopwords
    dataframe[column] = dataframe[column].apply(lambda x: ' '.join([word for word in x.split() if word.lower() not in stop_words]))
    #removing awkward photo links
    dataframe[column] = dataframe[column].apply(lambda x: ' '.join([word for word in x.split() if not word.startswith('pictwittercom')]))
    # stem text
    # dataframe[column] = dataframe[column].apply(lambda x: ' '.join([stemmer.stem(word) for word in x.split()]))
    # make lowercase
    dataframe[column] = dataframe[column].str.lower()
    return dataframe[column]

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\vladp\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [120]:
complete_news_df['TitleProcessed'] = preprocess_text_for_column(complete_news_df,'title')

C:\Users\vladp\AppData\Local\Temp\ipykernel_10388\2775769900.py:9: FutureWarning:

The default value of regex will change from True to False in a future version.

C:\Users\vladp\AppData\Local\Temp\ipykernel_10388\2775769900.py:11: FutureWarning:

The default value of regex will change from True to False in a future version.



In [122]:
complete_news_df['TitleProcessed'].sample(20)

16780    real housewives mysteries stolen homes mystery lovers friendshipending fights rocked franchise
15577                                             romeo santos proudly unveils wax figure fans petition
15130                                         happens abbey recap murrays slut marissas cheater edition
2252                                                   aritzia says meghan markle boosted earnings last
10072                                                            meghan trainor planning winter wedding
6754                                                        wags atlanta season 1 episode 2 dating game
102                                    selena gomez justin theroux may dating jennifer aniston freaking
748                               cw star caity lotz fights back online body shamers empowering message
8985                                              meanings behind kanye kim kardashian wests kids names
16414                                                          s

In [123]:
from collections import Counter

def count_words_frequency(dataframe,column):
    words = [word for title in dataframe[column] for word in title.split()]
    words_counter = Counter(words)
    words_df = pd.DataFrame(words_counter.items(),columns=['Word','Frequency'])
    return words_df

In [124]:
def create_dataframe_with_statistical_values_for_words(dataframe,columnWithWords):
    real_words_frequency = count_words_frequency(dataframe[dataframe['label']==1],columnWithWords)
    real_words_frequency['label'] = 1

    fake_words_frequency = count_words_frequency(dataframe[dataframe['label']==0],columnWithWords)
    fake_words_frequency['label'] = 0

    complete_freqs_dataframe = pd.concat([real_words_frequency,fake_words_frequency])
    temp_freq_dataframe = complete_freqs_dataframe[['Word','Frequency']].groupby('Word').sum().reset_index().rename(columns={'Frequency':'Total'})
    complete_freqs_dataframe = complete_freqs_dataframe.merge(temp_freq_dataframe,left_on='Word',right_on='Word',how='left')

    complete_freqs_dataframe['FrequencyRelative'] = complete_freqs_dataframe['Frequency']/complete_freqs_dataframe['Total']
    complete_freqs_dataframe = complete_freqs_dataframe.merge(complete_freqs_dataframe[complete_freqs_dataframe['label']==1][['Word','FrequencyRelative']].rename(columns={'FrequencyRelative':'FrequencyPositive'}),left_on='Word',right_on='Word',how='left')
    complete_freqs_dataframe = complete_freqs_dataframe.merge(complete_freqs_dataframe[complete_freqs_dataframe['label']==0][['Word','FrequencyRelative']].rename(columns={'FrequencyRelative':'FrequencyNegative'}),left_on='Word',right_on='Word',how='left')
    complete_freqs_dataframe.fillna(0,inplace=True)

    return complete_freqs_dataframe

In [125]:
complete_news_df[complete_news_df['id'].str.startswith('polit')]['label'].value_counts()

1    624
0    432
Name: label, dtype: int64

In [126]:
complete_freqs_for_news_polit = create_dataframe_with_statistical_values_for_words(complete_news_df[complete_news_df['id'].str.startswith('polit')],'TitleProcessed')

In [127]:
complete_freqs_for_news_polit.sample(2)

Word  Frequency  label  Total  FrequencyRelative  FrequencyPositive  FrequencyNegative
1724  women          1      1      7           0.142857           0.142857           0.857143
3516  ended          1      0      1           1.000000           0.000000           1.000000

In [128]:
px.bar(complete_freqs_for_news_polit.sort_values(['Total','label'],ascending=False),x='Word',y='Frequency',color='label')

In [130]:
px.bar(complete_freqs_for_news_polit[complete_freqs_for_news_polit['Total']>10].sort_values(['FrequencyNegative','label'],ascending=False),x='Word',y='FrequencyRelative',color='label')

In [131]:
complete_freqs_for_news_celeb = create_dataframe_with_statistical_values_for_words(complete_news_df[complete_news_df['id'].str.startswith('gos')],'TitleProcessed')

In [132]:
px.bar(complete_freqs_for_news_celeb.sort_values(['Total','label'],ascending=False),x='Word',y='Frequency',color='label')

In [135]:
px.bar(complete_freqs_for_news_celeb[complete_freqs_for_news_celeb['Total']>200].sort_values(['FrequencyNegative','label'],ascending=False),x='Word',y='FrequencyRelative',color='label')

In [136]:

dfs_dict['tweets_gossipcop_fake']['label']=0
dfs_dict['tweets_gossipcop_real']['label']=1
dfs_dict['tweets_politifact_fake']['label']=0
dfs_dict['tweets_politifact_real']['label']=1

news_dfs = [dfs_dict['tweets_gossipcop_fake'],dfs_dict['tweets_gossipcop_real'],dfs_dict['tweets_politifact_fake'],dfs_dict['tweets_politifact_real']]

complete_tweets_df = pd.concat(news_dfs)

In [137]:
complete_tweets_df.sample(10)

news_id             tweet_id                                                                                                                                                                                                                                                                                     text  label
92437    politifact13854   839178592508608512                                                                                                                                                RT SnopesVideo: Fact Check: FBI Issues Warrant for Obama’s Arrest After Confirming Illegal Trump Tower Wiretap?F… https://t.co/EE5bGX6org      0
606128  gossipcop-888389  1019251335110320132                                                                                                                                                                                          MAMMA MIA! HERE WE GO AGAIN (2018) | Behind the Scenes of Musical Movie https://t.co/pVvb9NlM2C      1
561578  gossipcop-846462   857605902035111937                                                                                                                                                                                       Robert De Niro Makes His Snapchat Debut and It's as Amazing as You'd Think https://t.co/NeB9RH9AvD      1
403263    politifact8629   805730068974759936                                                                                                                                                                                                                               @CrockettWDSU you're up early again. No rest for the weary      1
120984  gossipcop-924126   979562159339384832                                                                                                                                                                                         Denim Trends Sienna Miller, Bella Hadid and More Are Wearing This Spring https://t.co/sMASM50FYw      1
386350  gossipcop-860652   875108679485411330                                                                                                                                                                                                       TV Scoop Awards: Vote for the Best Drama Actor and Actress https://t.co/GXaarC5SQV      1
62774   gossipcop-794053   775546915811233793                                                                                                                                                 Ryan Lochte Gets Rushed by Protesters After Dancing With the Stars Performance - E! Online: E! OnlineRyan Loc... https://t.co/zdMJHJWvt8      1
166944  gossipcop-952758  1019603257667276807            The Dark Knight Turns 10: Remembering Heath Ledger's Iconic Role One of the most memorable lines from The Dark Knight comes from Harvey Dent: "You either die a hero, or you live long enough to see yourself become the villain." But the Two-Face...https://t.co/F9ipW7pXqz      1
381181  gossipcop-936991   997893413180723200  The Greatest Moments From the Royal Wedding, From the Smiling Page Boy to Candid Celebrity Reactions May 19, a special day. Prince Harry and Meghan Markle tied the knot at St. George's Chapel at Windsor Castle and there was no shortage of special moments… https://t.co/cADiWY6Prd      1
160801     politifact439   984072011214442497                                                                                                                      Mark Zuckerberg is beginning his testimony before the House Energy and Commerce Committee. His opening remarks are pretty much the same as yesterday at the senate.      1

In [139]:
complete_tweets_df.shape

(1716351, 4)

In [140]:
complete_tweets_df['TextCleared'] = preprocess_text_for_column(complete_tweets_df,'text')

C:\Users\vladp\AppData\Local\Temp\ipykernel_10388\2775769900.py:9: FutureWarning:

The default value of regex will change from True to False in a future version.

C:\Users\vladp\AppData\Local\Temp\ipykernel_10388\2775769900.py:11: FutureWarning:

The default value of regex will change from True to False in a future version.



In [141]:
del complete_tweets_df['text']

In [142]:
complete_tweets_df.sample(10)

news_id             tweet_id  label                                                                                                                                                                                                         TextCleared
389232      gossipcop-937243   997956194894462977      1                                                                                                                                              adele sends prince harry touching message princess diana royal wedding
492262      gossipcop-926287   983571117066637312      1  prince harry meghan markles engagement photographer spills details joyful shoot sometimes picture worth thousand words sometimes picture catapults career another stratosphere alexi lubomirski adept shutterbug w
468113      gossipcop-927561   985802053728591874      1                                                                                                                                                                               john cena nikki bella split six years
306404      gossipcop-954167  1021520462214586368      1                          stormy daniels husband glendon crain files divorce stormy daniels glendon crain going separate ways e news confirm crain musician former adult star filed divorce daniels july 18 attorney
129787  gossipcop-1686501961  1055160177320701952      0                                                             hey todayshow remember clues matt lauer big jerk nothing years well long take realize megyn kelly even bigger ignorant jerk finally fire everybodytalks
106347   gossipcop-534111552   969195920138088449      0                                                                                                                                                                                    cual doping lo dijo el reportero
158706  gossipcop-2710044770  1036829136986230784      0                                                                                                                                                            kendall jenner e super sapatao ta mentindo pra ela mesmo
69376         politifact7618  1054837368006631424      1                                                                                                                                        cnn lead w jake tapper 102318 cnn president trump news today october 23 2018
179527  gossipcop-3029477153   239815736921575424      0                                                                                                                                                  brad pitt 8220livid8221 angelina jolie fight maddox8217s dirt bike
126347  gossipcop-9520738949  1036792990163976194      0                                                                                                                                 guess kimmy jimmy arent together anymore bb found kevin costner lady bettercallsaul

In [144]:
complete_tweets_df.nunique()

news_id          22959
tweet_id       1435836
label                2
TextCleared     828021
dtype: int64

In [145]:
complete_tweets_df.drop_duplicates(subset=['TextCleared'],inplace=True)

In [148]:
complete_tweets_df.shape

(828021, 4)

In [147]:
complete_tweets_df.sample(10)

news_id             tweet_id  label                                                                                                                                                                                                    TextCleared
435797      gossipcop-905170   951098553480503297      1                                                                                                              hugh grant 57 expecting fifth child seven years girlfriend anna eberstein pictwittercomk2ldsmp2x7
288023  gossipcop-9495394238  1036451586514477056      0                                                                                                                        iraq war war based lies millions murdered lets think man cute sudden gives candy mobama
440130      gossipcop-850207   868175742365908992      1                                                                                     pictures pippa middleton marries james matthewsthe duchess cambridges sister pippa middleton married financier james matth
583509      gossipcop-897766   937470534358482945      1                                                                                                                               ed sheeran says beyonce changes email address every week pictwittercom3zfq9tfwjl
165946  gossipcop-2029753949  1037369898647912448      0                                                                                                                          apologizing bullshit like back tracking media relationships kris jenner shit annoying
476880      gossipcop-876873   902998421874900992      1                                                                                                                kenya moore fires back haters mocked marriage enough enough kenya moore vowed fight back haters
26614   gossipcop-1716370499  1043886157640216581      0                                     interesting went jamie dornans tag theres posts way btw even though dakota johnsons movie premiere yesterday go tags jd almost like fans trying take ride success pathetic
174716       politifact12104  1021373615164534787      1  every eatsmart bathroomscale four high precision sensors one feet suggest placing scale hard flat surface always avoid carpet optimal surfaces include ceramic porcelain tile hard wood concrete digitalscale
3397        gossipcop-910052   958071753938493441      1                                                                                                          luis fonsi shares message fans taking home grammy well continue share culture pictwittercom2tedzojt8c
3866         politifact14742   654057478452326400      0                                                                                                                                                                       snapchat shutting video hub snap channel

In [150]:
complete_tweets_df['TextCleared'] = preprocess_text_for_column(complete_tweets_df,'TextCleared')

C:\Users\vladp\AppData\Local\Temp\ipykernel_10388\3910336423.py:9: FutureWarning:

The default value of regex will change from True to False in a future version.

C:\Users\vladp\AppData\Local\Temp\ipykernel_10388\3910336423.py:11: FutureWarning:

The default value of regex will change from True to False in a future version.



In [151]:
complete_tweets_df.drop_duplicates(subset=['TextCleared'],inplace=True)

In [152]:
complete_tweets_df.shape

(679798, 4)

In [154]:
complete_freqs_for_tweets_polit = create_dataframe_with_statistical_values_for_words(complete_tweets_df[complete_tweets_df['news_id'].str.startswith('polit')],'TextCleared')

In [159]:
px.bar(complete_freqs_for_tweets_polit[complete_freqs_for_tweets_polit['Total']>4500].sort_values(['Total','label'],ascending=False),x='Word',y='Frequency',color='label')

In [163]:
px.bar(complete_freqs_for_tweets_polit[complete_freqs_for_tweets_polit['Total']>4500].sort_values(['FrequencyNegative','label'],ascending=False),x='Word',y='FrequencyRelative',color='label')

In [164]:
complete_freqs_for_tweets_celeb = create_dataframe_with_statistical_values_for_words(complete_tweets_df[complete_tweets_df['news_id'].str.startswith('gos')],'TextCleared')

In [174]:
px.bar(complete_freqs_for_tweets_celeb[complete_freqs_for_tweets_celeb['Total']>500].sort_values(['Total','label'],ascending=False)[:200],x='Word',y='Frequency',color='label')

In [179]:
px.bar(complete_freqs_for_tweets_celeb[complete_freqs_for_tweets_celeb['Total']>2000].sort_values(['FrequencyNegative','label'],ascending=False)[:150],x='Word',y='FrequencyRelative',color='label')